<br>


# Chicago Data
Alexander Kowsik

<br>
<br>

In [403]:
import pandas as pd
import geopandas as gpd
import numpy as np
import geojson

import requests
from bs4 import BeautifulSoup

import geocoder
from geopy.geocoders import Nominatim

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium
from folium.plugins import HeatMap

In [404]:
CLIENT_ID = 'EWPJTHBD35PF21MKIXYRV3IJU5C4IBQCG3P2TDI0EA4MEILP'
CLIENT_SECRET = 'YA5SHVIQMVIS5JKOVYVYDTBWUVMDSXMMPZW11QCMUWDYKL3F'
VERSION = '20200505'
RADIUS = 500

<br>

## 0. Create a map of Chicagos community areas

### Scraping the community areas (numbers and names)

In [405]:
chicago_data = gpd.read_file('data/Boundaries - Community Areas (current).geojson')
chicago_data.head()

community area     shape_area perimeter area_num_1 area_numbe  \
0          DOUGLAS    0  46004621.1581         0         35         35   
1          OAKLAND    0  16913961.0408         0         36         36   
2      FULLER PARK    0  19916704.8692         0         37         37   
3  GRAND BOULEVARD    0  48492503.1554         0         38         38   
4          KENWOOD    0  29071741.9283         0         39         39   

  comarea_id comarea      shape_len  \
0          0       0  31027.0545098   
1          0       0  19565.5061533   
2          0       0  25339.0897503   
3          0       0  28196.8371573   
4          0       0  23325.1679062   

                                            geometry  
0  MULTIPOLYGON (((-87.60914 41.84469, -87.60915 ...  
1  MULTIPOLYGON (((-87.59215 41.81693, -87.59231 ...  
2  MULTIPOLYGON (((-87.62880 41.80189, -87.62879 ...  
3  MULTIPOLYGON (((-87.60671 41.81681, -87.60670 ...  
4  MULTIPOLYGON (((-87.59215 41.81693, -87.59215 ...

In [406]:
chicago_data.dtypes

community       object
area            object
shape_area      object
perimeter       object
area_num_1      object
area_numbe      object
comarea_id      object
comarea         object
shape_len       object
geometry      geometry
dtype: object

In [407]:
for col in ['area', 'perimeter', 'area_num_1', 'area_numbe']:
    chicago_data[col] = chicago_data[col].astype('int64')

In [408]:
address = 'Chicago'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Chicago are 41.8755616, -87.6244212.


In [409]:
map_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)

with open('data/Boundaries - Community Areas (current).geojson') as f:
    community_area_geodata = geojson.load(f)
    
folium.GeoJson(community_area_geodata).add_to(map_chicago)

map_chicago

<br>

## 1. Crime data

In [410]:
crime_data = pd.read_csv('data/crimes.csv')
crime_data['Community Area'].unique()

array([23, 58, 27, 66, 49, 24,  8, 56, 55, 31, 15, 19, 45, 26, 67, 68, 22,
       25, 35, 33,  6, 75, 43, 32, 48, 72, 36, 50, 46,  3, 41, 13, 63, 69,
       42, 64, 71, 30, 44, 29, 60,  1, 14, 47, 28, 16,  7, 70, 54, 21, 62,
        5, 51, 61, 77, 57, 53,  2, 40, 34, 76, 39, 73,  4, 38, 11, 52, 20,
       74, 59, 17, 65, 10,  9, 18, 37, 12])

### Join community areas with crimes dataset

In [411]:
crime_data = crime_data.merge(chicago_data[['area_numbe', 'community']], 
                              how='inner', 
                              left_on='Community Area', 
                              right_on='area_numbe')
crime_data.head()

ID Case Number                    Date                   Block  IUCR  \
0  12042655    JD222392  01/01/2019 12:01:00 AM     011XX N HARDING AVE  1754   
1  11857593    JC468729  01/01/2019 12:01:00 AM      011XX N KEDZIE AVE  0810   
2  11552605    JC100030  01/01/2019 12:01:00 AM  004XX N MONTICELLO AVE  143A   
3  11552687    JC100202  01/01/2019 12:30:00 AM     015XX N KEDVALE AVE  1310   
4  11552696    JC100083  01/01/2019 12:45:00 AM   035XX W FRANKLIN BLVD  143A   

                 Primary Type  \
0  OFFENSE INVOLVING CHILDREN   
1                       THEFT   
2           WEAPONS VIOLATION   
3             CRIMINAL DAMAGE   
4           WEAPONS VIOLATION   

                                         Description Location Description  \
0  AGGRAVATED SEXUAL ASSAULT OF CHILD BY FAMILY M...            APARTMENT   
1                                          OVER $500                OTHER   
2                           UNLAWFUL POSS OF HANDGUN                ALLEY   
3                                        TO PROPERTY            RESIDENCE   
4                           UNLAWFUL POSS OF HANDGUN             SIDEWALK   

   Arrest  Domestic  ...  FBI Code  X Coordinate  Y Coordinate  Year  \
0   False      True  ...        02     1149847.0     1907223.0  2019   
1   False     False  ...        06     1154827.0     1907315.0  2019   
2    True     False  ...        15     1151958.0     1902815.0  2019   
3   False     False  ...        14     1148429.0     1910068.0  2019   
4    True     False  ...        15     1152737.0     1903107.0  2019   

               Updated On   Latitude  Longitude  \
0  05/06/2020 03:52:26 PM  41.901334 -87.725041   
1  10/16/2019 04:05:26 PM  41.901488 -87.706747   
2  01/10/2019 03:16:50 PM  41.889196 -87.717404   
3  01/10/2019 03:16:50 PM  41.909168 -87.730176   
4  01/10/2019 03:16:50 PM  41.889982 -87.714535   

                        Location area_numbe      community  
0  (41.901333719, -87.725041451)         23  HUMBOLDT PARK  
1  (41.901487821, -87.706746857)         23  HUMBOLDT PARK  
2  (41.889196391, -87.717403722)         23  HUMBOLDT PARK  
3   (41.90916816, -87.730176471)         23  HUMBOLDT PARK  
4   (41.889982289, -87.71453517)         23  HUMBOLDT PARK  

[5 rows x 24 columns]

In [412]:
crime_data['Community Area'].unique()

array([23, 58, 27, 66, 49, 24,  8, 56, 55, 31, 15, 19, 45, 26, 67, 68, 22,
       25, 35, 33,  6, 75, 43, 32, 48, 72, 36, 50, 46,  3, 41, 13, 63, 69,
       42, 64, 71, 30, 44, 29, 60,  1, 14, 47, 28, 16,  7, 70, 54, 21, 62,
        5, 51, 61, 77, 57, 53,  2, 40, 34, 76, 39, 73,  4, 38, 11, 52, 20,
       74, 59, 17, 65, 10,  9, 18, 37, 12])

In [413]:
crime_data.dropna(subset=['Latitude', 'Longitude'], inplace=True)

In [414]:
# heat_data = [[row['Latitude'], row['Longitude']] for index, row in crime_data.iterrows()]

In [415]:
"""
heat_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)

folium.GeoJson(community_area_geodata).add_to(heat_chicago)

HeatMap(heat_data,
        min_opacity=0.5,
        max_zoom=18, 
        max_val=1.0, 
        radius=15,
        blur=20,
        gradient=None,
        overlay=True).add_to(heat_chicago)

heat_chicago
"""

'\nheat_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)\n\nfolium.GeoJson(community_area_geodata).add_to(heat_chicago)\n\nHeatMap(heat_data,\n        min_opacity=0.5,\n        max_zoom=18, \n        max_val=1.0, \n        radius=15,\n        blur=20,\n        gradient=None,\n        overlay=True).add_to(heat_chicago)\n\nheat_chicago\n'

<br>

## 2. Median household income

In [416]:
url = "https://www.homesnacks.net/richest-neighborhoods-in-chicago-128972"

page = requests.get(url).text
soup = BeautifulSoup(page, 'html.parser')

In [417]:
table = soup.find('table')
income_data = pd.read_html(str(table))[0]
income_data.head()

Rank  Neighborhood Median Household Income<
0     1   Forest Glen                 $112,032
1     2  Lincoln Park                  $99,720
2     3  North Center                  $99,384
3     4       Beverly                  $99,102
4     5   Edison Park                  $98,327

In [418]:
income_data['Neighborhood'] = income_data['Neighborhood'].str.upper()

In [419]:
income_data['Median Household Income<'] = \
    income_data['Median Household Income<'].apply(lambda x: int(x[1:].replace(',', '')))

income_data.head()

Rank  Neighborhood  Median Household Income<
0     1   FOREST GLEN                    112032
1     2  LINCOLN PARK                     99720
2     3  NORTH CENTER                     99384
3     4       BEVERLY                     99102
4     5   EDISON PARK                     98327

In [420]:
maximum = income_data['Median Household Income<'].max()
maximum

112032

In [421]:
def convert_to_hex(rgba_color):
    green = '00'
    blue = '00'
    
    red = str(hex(int(rgba_color*255)))[2:].capitalize()

    if red=='0':
        red = '00'

    return '#'+ red + green + blue

In [422]:
income_data['income_colors'] = income_data['Median Household Income<'].apply(lambda x: convert_to_hex(x/maximum)).tolist()
income_data['income_colors'][0:10]

0    #Ff0000
1    #E20000
2    #E20000
3    #E10000
4    #Df0000
5    #Df0000
6    #De0000
7    #D00000
8    #C80000
9    #B90000
Name: income_colors, dtype: object

In [423]:
chicago_data = chicago_data.merge(income_data, 
                                  how='left', 
                                  left_on='community', 
                                  right_on='Neighborhood')
chicago_data.head()

community  area     shape_area  perimeter  area_num_1  area_numbe  \
0          DOUGLAS     0  46004621.1581          0          35          35   
1          OAKLAND     0  16913961.0408          0          36          36   
2      FULLER PARK     0  19916704.8692          0          37          37   
3  GRAND BOULEVARD     0  48492503.1554          0          38          38   
4          KENWOOD     0  29071741.9283          0          39          39   

  comarea_id comarea      shape_len  \
0          0       0  31027.0545098   
1          0       0  19565.5061533   
2          0       0  25339.0897503   
3          0       0  28196.8371573   
4          0       0  23325.1679062   

                                            geometry  Rank     Neighborhood  \
0  MULTIPOLYGON (((-87.60914 41.84469, -87.60915 ...  50.0          DOUGLAS   
1  MULTIPOLYGON (((-87.59215 41.81693, -87.59231 ...  59.0          OAKLAND   
2  MULTIPOLYGON (((-87.62880 41.80189, -87.62879 ...  76.0      FULLER PARK   
3  MULTIPOLYGON (((-87.60671 41.81681, -87.60670 ...  55.0  GRAND BOULEVARD   
4  MULTIPOLYGON (((-87.59215 41.81693, -87.59215 ...  38.0          KENWOOD   

   Median Household Income< income_colors  
0                   39212.0       #590000  
1                   35228.0       #500000  
2                   22962.0       #340000  
3                   36187.0       #520000  
4                   47591.0       #6c0000

In [424]:
chicago_data.to_file('data/community_areas_with_colors.geojson', driver='GeoJSON')

with open('data/community_areas_with_colors.geojson') as f:
    community_area_geodata_colored = geojson.load(f)

In [425]:
income_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)

folium.GeoJson(community_area_geodata).add_to(income_chicago)

folium.GeoJson(
    community_area_geodata_colored,
    style_function= lambda feature: {
        'fillColor': feature['properties']['income_colors'],
        'color' : feature['properties']['income_colors'],
        'weight' : 1,
        'fillOpacity' : 0.5,
        }
    ).add_to(income_chicago)

income_chicago

<br>

## 3. Rent prices

In [426]:
url = "https://www.rentcafe.com/average-rent-market-trends/us/il/chicago"

page = requests.get(url).text
soup = BeautifulSoup(page, 'html.parser')

In [427]:
table = soup.find('table' , {'id' : "MarketTrendsAverageRentTable"})
rent_data = pd.read_html(str(table))[0]
rent_data.head()

Neighborhood Average Rent
0    The Island         $562
1        Austin         $562
2  West Pullman         $612
3      Rosemoor         $612
4      Roseland         $612

In [428]:
rent_data['Average Rent'] = \
    rent_data['Average Rent'].apply(lambda x: int(x[1:].replace(',', '')))

rent_data.head()

Neighborhood  Average Rent
0    The Island           562
1        Austin           562
2  West Pullman           612
3      Rosemoor           612
4      Roseland           612

In [429]:
rent_data['Neighborhood'] = rent_data['Neighborhood'].str.upper()
rent_data['Average Rent'] = rent_data['Average Rent'].dropna()

In [431]:
maximum = rent_data['Average Rent'].max()
rent_data['rent_colors'] = rent_data['Average Rent'].apply(lambda x: convert_to_hex(x/maximum)).tolist()
rent_data['rent_colors'][0:10]

0    #370000
1    #370000
2    #3c0000
3    #3c0000
4    #3c0000
5    #3c0000
6    #3c0000
7    #3c0000
8    #3c0000
9    #3c0000
Name: rent_colors, dtype: object

In [432]:
chicago_data = chicago_data.merge(rent_data, 
                                  how='left', 
                                  left_on='community', 
                                  right_on='Neighborhood')
chicago_data.head()

community  area     shape_area  perimeter  area_num_1  area_numbe  \
0          DOUGLAS     0  46004621.1581          0          35          35   
1          OAKLAND     0  16913961.0408          0          36          36   
2      FULLER PARK     0  19916704.8692          0          37          37   
3  GRAND BOULEVARD     0  48492503.1554          0          38          38   
4          KENWOOD     0  29071741.9283          0          39          39   

  comarea_id comarea      shape_len  \
0          0       0  31027.0545098   
1          0       0  19565.5061533   
2          0       0  25339.0897503   
3          0       0  28196.8371573   
4          0       0  23325.1679062   

                                            geometry  Rank   Neighborhood_x  \
0  MULTIPOLYGON (((-87.60914 41.84469, -87.60915 ...  50.0          DOUGLAS   
1  MULTIPOLYGON (((-87.59215 41.81693, -87.59231 ...  59.0          OAKLAND   
2  MULTIPOLYGON (((-87.62880 41.80189, -87.62879 ...  76.0      FULLER PARK   
3  MULTIPOLYGON (((-87.60671 41.81681, -87.60670 ...  55.0  GRAND BOULEVARD   
4  MULTIPOLYGON (((-87.59215 41.81693, -87.59215 ...  38.0          KENWOOD   

   Median Household Income< income_colors Neighborhood_y  Average Rent  \
0                   39212.0       #590000            NaN           NaN   
1                   35228.0       #500000        OAKLAND        1274.0   
2                   22962.0       #340000    FULLER PARK        1171.0   
3                   36187.0       #520000            NaN           NaN   
4                   47591.0       #6c0000        KENWOOD        1578.0   

  rent_colors  
0         NaN  
1     #7c0000  
2     #720000  
3         NaN  
4     #9a0000

In [434]:
chicago_data.to_file('data/community_areas_with_colors.geojson', driver='GeoJSON')

with open('data/community_areas_with_colors.geojson') as f:
    community_area_geodata_rents = geojson.load(f)

In [435]:
rent_chicago = folium.Map(location=[latitude, longitude], zoom_start=10)

folium.GeoJson(community_area_geodata).add_to(rent_chicago)

folium.GeoJson(
    community_area_geodata_rents,
    style_function= lambda feature: {
        'fillColor': feature['properties']['rent_colors'],
        'color' : feature['properties']['rent_colors'],
        'weight' : 1,
        'fillOpacity' : 0.5,
        }
    ).add_to(rent_chicago)

rent_chicago

<